# Biomass Yield and Spectral Trends

```
date: 2025-01-15
authors:
    - name: Brookie Guzder-Williams
affiliations:
    - University of California Berkeley, The Eric and Wendy Schmidt Center for Data Science & Environment
license: CC-BY-4.0
```

This notebook uses DSE's [Spectral Trend Database](https://github.com/SchmidtDSE/spectral_trend_database) (STDB) to
produce and interactive chart displaying Biomass Yield vs a number of different spectral incides over time.

1. Fetch Data for a random point: We use STDS's [query module](https://github.com/SchmidtDSE/spectral_trend_database/blob/main/spectral_trend_database/query.py) and in particular the [`QueryConstructor`](https://github.com/SchmidtDSE/spectral_trend_database/blob/54146cf058e2180829e2c169b37c18ddf62b68a0/spectral_trend_database/query.py#L21-L114) to generate a ...
2. Build Chart
3. Save Chart JSON to improve responsiveness of chart


---

### IMPORTS


In [1]:
from importlib import reload
from typing import Callable, Union, Optional, Literal, TypeAlias, Sequence, Any
import re
from pprint import pprint
import random
import pandas as pd
import numpy as np
import xarray as xr
import tensorflow as tf
from IPython.display import HTML
import matplotlib.pyplot as plt
import seaborn as sns
import altair as alt
from spectral_trend_database.config import config as c
from spectral_trend_database import query
from spectral_trend_database import utils
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import HistGradientBoostingClassifier
from sklearn import metrics


---

### CONFIG

In [2]:
BQ_PREFIX = 'dse-regenag.SpectralTrendDatabase'
SAMPLES_TABLE = 'SAMPLE_POINTS'
CROP_TYPE_TABLE = 'CDL_CROP_TYPE'
YIELD_TABLE = 'QDANN_YIELD'
INDICES_TABLE = 'SMOOTHED_INDICES_V1'

In [3]:
SAMPLE_ID = '9zphqkb3hh8'
CHART_DATA_PATH = 'spectral_trends.chart_data.json'
SAMPLE_FRAC = 0.0005

In [4]:
YEAR_START = 2008
YEAR_END = 2018
START_MMDD = '11-01'
END_MMDD = START_MMDD

In [5]:
ATTR_COLS = [
    'sample_id',
    'lon',
    'lat']
LIST_ATTRS = [
    'year',
    'biomass',
    'crop_type']
IDENT_DATE_COLUMNS = ['sample_id', 'year', 'date']


---

### HELPER METHODS


In [6]:
def print_list(lst, max_len=7, view_size=3, sep=', ', connector=' ... '):
    size = len(lst)
    if size <= max_len:
        lst_str = sep.join(lst)
    else:
        head = sep.join(lst[:view_size])        
        tail = sep.join(lst[-view_size:])
        lst_str = f'{head}{connector}{tail}  [{size}]'
    print(lst_str)

def line(marker='-', length=100):
    print(marker*length)

---

In [7]:
SMOOTHED_INDICES_COLUMNS = query.column_names(INDICES_TABLE, run_query=True)
INDICES = [c for c in SMOOTHED_INDICES_COLUMNS if c not in IDENT_DATE_COLUMNS]
INDICES = sorted(INDICES)
print_list(INDICES)

afri1600, atsavi, blue ... tvi, wdrvi, wet  [42]



---

### 1. Fetch Data

In [8]:
query = reload(query)
def fetch_yield_and_trend_data(
        year_start: int,
        year_end: Optional[int] = None,
        sample_id: Optional[Union[list[str], str]] = None,
        print_sql: Optional[bool] = False,
        limit: Optional[int] = None) -> pd.DataFrame:
    """
    Builds and Executes a SQL Query to get all data
    form a given set of sample_ids during a specified time 
    period.
    
    Args: 
        year_start (int): start year to select data
        year_end (Optional[int] = None): 
            last year to select data from (inclusive). if None use <year_start>
        sample_id (Optional[Union[list[str], str]] = None)
            sample_id or list of sample-ids of data to select. if none select 
            from all samples.
        print_sql (Optional[bool] = False)
        limit (Optional[int] = None)

    Returns:
        pd.DataFrame of smoothed-spectral-indices
    """
    if year_end is None: 
        year_end=year_start
    qc = query.QueryConstructor(
        SAMPLES_TABLE, 
        table_prefix=BQ_PREFIX,
        using=['sample_id'],  
        how='inner')
    qc.join(CROP_TYPE_TABLE, 'sample_id')
    qc.join(YIELD_TABLE, 'sample_id', 'year')
    qc.join(INDICES_TABLE, 'sample_id', 'year')
    if sample_id:
        if isinstance(sample_id, list):
            qc.where_in(sample_id=sample_id)
        else:
            qc.where(sample_id=sample_id)
    qc.where(INDICES_TABLE, year=year_start, year_op='>=')
    qc.where(INDICES_TABLE, year=year_end, year_op='<=')
    qc.orderby('date', table=INDICES_TABLE)
    df = query.run(sql=qc.sql(), print_sql=print_sql)
    return df

In [9]:
data = fetch_yield_and_trend_data(
    year_start=YEAR_START,
    year_end=YEAR_END,
    sample_id=SAMPLE_ID,
    print_sql=True)

print('shape:', data.shape)
data.sample(3)

[info] spectral_trend_database.query.run: SELECT * FROM `dse-regenag.SpectralTrendDatabase.SAMPLE_POINTS` INNER JOIN `dse-regenag.SpectralTrendDatabase.CDL_CROP_TYPE` USING (sample_id) INNER JOIN `dse-regenag.SpectralTrendDatabase.QDANN_YIELD` USING (sample_id, year) INNER JOIN `dse-regenag.SpectralTrendDatabase.SMOOTHED_INDICES_V1` USING (sample_id, year) WHERE `dse-regenag.SpectralTrendDatabase.SAMPLE_POINTS`.sample_id = "9zphqkb3hh8" AND `dse-regenag.SpectralTrendDatabase.SMOOTHED_INDICES_V1`.year >= 2008 AND `dse-regenag.SpectralTrendDatabase.SMOOTHED_INDICES_V1`.year <= 2018 ORDER BY `dse-regenag.SpectralTrendDatabase.SMOOTHED_INDICES_V1`.date ASC
shape: (4018, 70)


sample_id  year    AWATER       ALAND  LSAD STATE_NAME STUSPS  GEOID  \
87    9zphqkb3hh8  2008  41749180  2214831300     6   Illinois     IL  17001   
3171  9zphqkb3hh8  2016  41749180  2214831300     6   Illinois     IL  17001   
2616  9zphqkb3hh8  2015  41749180  2214831300     6   Illinois     IL  17001   

             GEOIDFQ      NAMELSAD  ...       nli        date       nir  \
87    0500000US17001  Adams County  ... -0.586512  2008-03-28  0.182604   
3171  0500000US17001  Adams County  ...  0.287189  2016-09-06  0.366544   
2616  0500000US17001  Adams County  ... -0.592357  2015-03-01  0.161557   

           red      evi2       rdi       gli      blue      savi      rdvi  
87    0.127755  0.100365  1.372100 -0.018976  0.083984  0.101466  0.098648  
3171  0.055358  0.505738  0.374717  0.188207  0.031344  0.480154  0.456814  
2616  0.103375  0.110942  1.013374  0.009985  0.059007  0.115174  0.115191  

[3 rows x 70 columns]

In [10]:
utils = reload(utils)
ds = utils.rows_to_xr(
    data.drop_duplicates(['date']), 
    attr_cols=ATTR_COLS,
    list_cols=LIST_ATTRS,
    list_distinct_cols=['sample_id', 'year'])
ds

<xarray.Dataset>
Dimensions:           (date: 4018)
Coordinates:
  * date              (date) datetime64[ns] 2008-01-01 2008-01-02 ... 2018-12-31
Data variables: (12/63)
    AWATER            (date) int64 41749180 41749180 ... 41749180 41749180
    ALAND             (date) int64 2214831300 2214831300 ... 2214831300
    LSAD              (date) int64 6 6 6 6 6 6 6 6 6 6 6 ... 6 6 6 6 6 6 6 6 6 6
    STATE_NAME        (date) object 'Illinois' 'Illinois' ... 'Illinois'
    STUSPS            (date) object 'IL' 'IL' 'IL' 'IL' ... 'IL' 'IL' 'IL' 'IL'
    GEOID             (date) int64 17001 17001 17001 17001 ... 17001 17001 17001
    ...                ...
    evi2              (date) float64 0.08599 0.08581 0.08563 ... 0.1152 0.1153
    rdi               (date) float64 1.4 1.402 1.402 1.402 ... 1.293 1.312 1.329
    gli               (date) float64 -0.02605 -0.02586 ... -0.0173 -0.01883
    blue              (date) float64 0.08231 0.08179 0.08126 ... 0.05401 0.05502
    savi              (date) float64 0.0872 0.08706 0.08692 ... 0.1219 0.122
    rdvi              (date) float64 0.08482 0.08472 0.08463 ... 0.1248 0.1247
Attributes:
    sample_id:  9zphqkb3hh8
    lon:        -91.131076303
    lat:        40.1483591048
    year:       [2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, ...
    biomass:    [2139.8148148148, 12975.1851851852, 3437.3333333333, 10237.29...
    crop_type:  ['soy', 'corn', 'soy', 'corn', 'soy', 'corn', 'soy', 'corn', ...

In [11]:
yield_biomass = { y: b for y,b in zip(ds.year, ds.biomass)}
crop_types = { y: b for y,b in zip(ds.year, ds.crop_type)}
dvars = { k: ds[k].data for k in ds.data_vars }
chart_data = pd.DataFrame(dvars)
chart_data['date'] = ds.date.data
chart_data['idx'] = list(chart_data.index)
chart_data['year'] = chart_data.date.apply(lambda d: d.year)
chart_data['biomass'] = chart_data.year.apply(lambda y: yield_biomass.get(y, None))
chart_data['crop_type'] = chart_data.year.apply(lambda y: crop_types.get(y, 'soy'))


---

### CHART

In [12]:
S = 1.25
DEFAULT_INDEX = 'slavi'
HEIGHT = 400 * S
GRAPH_WIDTH = 600 * S
SI_COLOR = '#515e68'
SI_OPACITY = 0.6
YIELD_OPACITY = 0.5
TITLE_COLOR = '#333'
TITLE_SIZE = 22
TITLE_WEIGHT = 200
SUBTITLE_COLOR = '#aaa'
SUBTITLE_SIZE = 14
SOY_COLOR = '#4e9561'
CORN_COLOR = '#e2d644'

In [13]:
TITLE = 'SPECTRAL TRENDS'
SUBTITLE = 'exploring yield as a function of spectral indices'

In [14]:
#| label: nb.indices_vs_yield
#| placeholder: ../../assets/placeholders/indices_vs_yield.static.png
display(HTML("""
<style>
  span.vega-bind-name {
    color: #555;
    margin: 0 10px 0 60px;
    font-size: 20px;
  }
  .vega-bind label select {
    color: #555;
    font-size: 18px;
  }
</style>
"""))

# yield chart
yield_scale = alt.Scale(
    domain=[0.0, 14000],
    clamp=True
)
yield_color_scale = alt.Scale(
    domain=['soy', 'corn'], 
    range=[SOY_COLOR, CORN_COLOR])
yield_yaxis = alt.Axis(title='Biomass Yield', titleFontSize=18, titleColor=TITLE_COLOR, titleFontWeight=TITLE_WEIGHT)
yield_chart = alt.Chart(chart_data).encode(
    x=alt.X('date:T', title=None),
    y=alt.Y('biomass:Q', axis=yield_yaxis, scale=yield_scale),
    color=alt.Color('crop_type:N', scale=yield_color_scale)
).mark_area(
    filled=True,
    opacity=YIELD_OPACITY,
    interpolate='step-before')

# interactive spectral index chart
si_yaxis = alt.Axis(title='Spectral Index', titleFontSize=18, titleColor=TITLE_COLOR, titleFontWeight=TITLE_WEIGHT)
si_dropdown = alt.binding_select(
    options=INDICES,
    labels=[n.upper() for n in INDICES],
    name='Spectral Index: '.upper()
)
ycol_param = alt.param(
    value=DEFAULT_INDEX,
    bind=si_dropdown
)
si_chart = alt.Chart(chart_data).encode(
    x=alt.X('date:T', title=None),
    y=alt.Y('y:Q', axis=si_yaxis)
).properties(
    width=GRAPH_WIDTH,
    height=HEIGHT
).transform_calculate(
    y=f'datum[{ycol_param.name}]'
).add_params(
    ycol_param
).mark_area(
    fill=SI_COLOR,
    fillOpacity=SI_OPACITY
)


# display
title = alt.Title(
    TITLE,
    color=TITLE_COLOR,
    fontSize=TITLE_SIZE,
    fontWeight=TITLE_WEIGHT,
    subtitle=SUBTITLE,
    subtitleColor=SUBTITLE_COLOR,
    subtitleFontSize=SUBTITLE_SIZE)

chart = alt.layer(yield_chart, si_chart).resolve_scale(y='independent')
chart = chart.properties(
    title=title).configure_legend(
    title=None,
    labelFontSize=18,  
    labelColor=SUBTITLE_COLOR 
)
chart 

alt.LayerChart(...)